# Wheel on Inclined Plane

In [1]:
%matplotlib widget

In [2]:
from ipywidgets import FloatSlider, AppLayout, Label, HBox

In [3]:
import numpy

In [4]:
import time

In [5]:
from IPython.display import display, clear_output

In [6]:
from pysketcher import *

In [7]:
g = 9.81

In [8]:
def inclined_plane():
    theta = 30.
    L = 10.
    a = 1.
    xmin = 0
    ymin = -3

    drawing_tool.set_coordinate_system(xmin=xmin, xmax=xmin+1.5*L,
                                       ymin=ymin, ymax=ymin+L+1,
                                       #axis=True,
                                       instruction_file='tmp_mpl.py'
                                       )
    #drawing_tool.set_grid(True)
    fontsize = 18
    from math import tan, radians

    B = point(a+L, 0)
    A = point(a, tan(radians(theta))*L)
    
    wall = Wall(x=[A[0], B[0]], y=[A[1], B[1]], thickness=-0.25,
                transparent=False)

    angle = Arc_wText(r'$\theta$', center=B, radius=3,
                      start_angle=180-theta, arc_angle=theta,
                      fontsize=fontsize)
    angle.set_linecolor('black')
    angle.set_linewidth(1)

    ground = Line((B[0]-L/10., 0), (B[0]-L/2.,0))
    ground.set_linecolor('black')
    ground.set_linestyle('dashed')
    ground.set_linewidth(1)

    r = 1  # radius of wheel
    help_line = Line(A, B)
    x = a + 3*L/10.; y = help_line(x=x)
    contact = point(x, y)
    normal_vec = point(sin(radians(theta)), cos(radians(theta)))
    tangent_vec = point(cos(radians(theta)), -sin(radians(theta)))
    
    length = Distance_wText(A+normal_vec*2.5,B+normal_vec*2.5, '$L$')
    
    c = contact + r*normal_vec
    outer_wheel = Circle(c, r)
    outer_wheel.set_linecolor('blue')
    outer_wheel.set_filled_curves('blue')
    hole = Circle(c, r/2.)
    hole.set_linecolor('blue')
    hole.set_filled_curves('white')

    wheel = Composition({'outer': outer_wheel, 'inner': hole})
    wheel.set_shadow(4)

    drawing_tool.set_linecolor('black')
    N = Force(contact - 2*r*normal_vec, contact, r'$N$', text_pos='start')
    mg = Gravity(c, 3*r, text='$Mg$')

    x_const = Line(contact, contact + point(0,4))
    x_const.set_linestyle('dotted')
    x_const.rotate(-theta, contact)
    # or x_const = Line(contact-2*r*normal_vec, contact+4*r*normal_vec).set_linestyle('dotted')
    x_axis = Axis(start=contact+ 3.5*r*normal_vec, length=4*r,
                  label='$x$', rotation_angle=-theta)

    body  = Composition({'wheel': wheel, 'N': N, 'mg': mg})
    fixed = Composition({'length': length, 'angle': angle, 'inclined wall': wall,
                         'ground': ground,
                         'x start': x_const, 'x axis': x_axis})

    fig = Composition({'body': body, 'fixed elements': fixed})
    fig.draw()
    return (fig,normal_vec,tangent_vec,c)

def position(t):
    """Position of center point of wheel."""
    global tangent_vec,c
    return c + 0.5*g*t**2*tangent_vec

t = 0

def speed(displacement,dt):
    if dt != 0: 
        v = (displacement)/dt
        #print(v)
        v = numpy.sqrt(v[0]**2 + v[1]**2)
    else:
        v = 0
    return v
        
def move(change):
    global fig,t,label,x,x0,dt
    dt = change.new - t 
    t = change.new
    drawing_tool.erase()
    x = position(t)
    x0 = position(t-dt)
    displacement = x - x0    
    fig['body'].translate(displacement)
    fig.draw()
    label.value = f"v={speed(displacement,dt):.2f}"
    #drawing_tool.display()

In [9]:
slider = FloatSlider(
    orientation='horizontal',
    description='Time:',
    value=0.0,
    min=0.0,
    max=1.0,
    step = 1.0 / 30
)
slider.observe(move, 'value')

In [10]:
label = Label(value="0")

In [11]:
fig,normal_vec,tangent_vec,c = inclined_plane()
AppLayout(
    center=drawing_tool.mpl.gcf().canvas,
    footer=HBox([slider,label]),
    pane_heights=[0, 6, 1]
)
#drawing_tool.mpl.ion()

AppLayout(children=(HBox(children=(FloatSlider(value=0.0, description='Time:', max=1.0, step=0.033333333333333…

In [12]:
drawing_tool.mpl.ion()

In [ ]:
for t in numpy.linspace(0.0,1.0,100):
    slider.value = t
    print(t)
    clear_output(wait=True)

In [ ]:
drawing_tool.mpl.ioff()

In [ ]:
fig.show_hierarchy